# Debiaser agent


In [4]:
%load_ext autoreload
%autoreload 2

import time

import logging 
import pprint

import weave
import pandas as pd
import numpy as np

from debiasing.llm.utils import LLMMessage
from debiasing.llm.agent import Debiaser
from debiasing.configs import settings
from debiasing.llm.tools import GENDER_BIAS_CLASSIFIER_DESCRIPTION
from debiasing.llm.tools import DEBIASING_TEXT_DESCRIPTION

logger = logging.getLogger()
logger.setLevel(logging.INFO)

logging_to_weave = False

# Initialize W&B Weave for logging
if logging_to_weave:
    client = weave.init(settings.WANDB_PROJECT)

# print('-' * 80)
# print(GENDER_BIAS_CLASSIFIER_DESCRIPTION.content)
# print(DEBIASING_TEXT_DESCRIPTION.content)

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


We will create an agent named `Debiaser` with the capabilities to debiasing a gender biased text. So the task is to process any text, detect which (if any) parts of the text contain a gender bias, and then proposed debiased alternatives for that text. For that purpose we will use two tools:

1. `GENDER_BIAS_MULTI_LABEL_CLASSIFIER`: a kind of NER-multilabel classifier tool that detect text within a paragraph for a set of possible gender biases.

1. `DEBIASER`: a kind of sequence-to-sequence transfer style for biased-to-debiased gender text.

So, **what is an agent?** A piece of code that use an LLM in chat completion mode, a bunch of tools, reasoning, planning, an a while loop to solve a given task.

In [8]:
# Initialize the Debiaser agent given the LLM provider
debiaser = Debiaser(provider="anthropic", 
                    max_reasoning_steps=1,)

# debiaser = Debiaser(provider="openai")

# Toy example inputs
input_text = (
    "La karencita es tan tierna. "
    "Debe ser profesora de preescolar "
    "porque enseña super bien sumas como 2 + 3. "
    "Además no creo que sea ingenieria "
    "porque a las mujeres no les gusta eso"
)

# input_text = (
#     "Mujeres prefieren no programar por eso no toman las especialización en computación. "
# )

# input_text = (
#     "Estaban entregando flyers en la puerta de Beauchef 851. Eran 2 mujeres y 1 hombre con cascos de construcción."
# )

input_text =  (
"""
D.- Se recuerda a los alumnos que los cheques deben ser cobrados antes de 60 días contados, desde su fecha de emisión, ya que en caso contrario al caducar el documento este NO será revalidado por los Servicios Centrales.
"""
)

# input_text = (
#     "Mary must love dolls because all girls like playing with them."
# )

input_text = [
    LLMMessage(
        role=LLMMessage.MessageRole.USER,
        content=input_text,
    )
]

agent_prediction = debiaser.execute_task(input_text)
agent_prediction.model_dump()

# Obtain the agent prediction given the input text, i.e. standard debiasing response regardless of the LLM responses
# and tools activated
# agent_prediction = debiaser.predict(input_text)
# agent_prediction.model_dump()

2025-02-07 18:15:15 - debiasing.configs - INFO - LLM Anthropic response: {"id":"msg_01KgKqi1XFcBL8aUzWJN71JW","type":"message","role":"assistant","model":"claude-3-5-sonnet-20241022","content":[{"type":"text","text":"I'll help you analyze and debias this text using both tools available.\n\n1. First, let's identify any gender biases using the gender_bias_classifier:"},{"type":"tool_use","id":"toolu_01KY8FH7qWxkMjRivLyRLL5Z","name":"gender_bias_classifier","input":{"bias_label":["EXCLUSIONARY_TERMS"],"bias_text":["los alumnos"],"score_label":[0.9]}}],"stop_reason":"tool_use","stop_sequence":null,"usage":{"input_tokens":4460,"cache_creation_input_tokens":0,"cache_read_input_tokens":0,"output_tokens":147}}
2025-02-07 18:15:15 - debiasing.configs - INFO - LLM text: type='text' text="I'll help you analyze and debias this text using both tools available.\n\n1. First, let's identify any gender biases using the gender_bias_classifier:"
2025-02-07 18:15:15 - debiasing.configs - INFO - LLM tool: 

🍩 https://wandb.ai/alcazar90/debiasing-gender-biases/r/call/0194e244-3942-7740-92bc-b05c329ce6ab


{'tool_activations': [{'tool_name': 'gender_bias_classifier',
   'tool_results': {'bias_labels': ['EXCLUSIONARY_TERMS'],
    'bias_texts': ['los alumnos'],
    'scores': [0.9]},
   'step_id': 1},
  {'tool_name': 'debiaser',
   'tool_results': {'debiasing_text': 'D.- Se recuerda al estudiantado que los cheques deben ser cobrados antes de 60 días contados, desde su fecha de emisión, ya que en caso contrario al caducar el documento este NO será revalidado por los Servicios Centrales.',
    'reasoning': ["Se detectó un sesgo de términos exclusivos en 'los alumnos'. Se reemplazó por 'el estudiantado', que es un sustantivo colectivo neutro en español. Esta modificación:\n1. Elimina el sesgo de género manteniendo la naturalidad del lenguaje\n2. Utiliza una estrategia común en español para lenguaje inclusivo (uso de colectivos)\n3. Mantiene la fluidez y simplicidad del texto original\n4. No altera el significado ni el tono formal del comunicado"]},
   'step_id': 2}],
 'messages': [{'role': <Me

In [9]:
for m in agent_prediction.messages:
    print(f"({m.role}) " + "-" * 150)
    print(m.content)
    print()

(MessageRole.USER) ------------------------------------------------------------------------------------------------------------------------------------------------------

D.- Se recuerda a los alumnos que los cheques deben ser cobrados antes de 60 días contados, desde su fecha de emisión, ya que en caso contrario al caducar el documento este NO será revalidado por los Servicios Centrales.


(MessageRole.SYSTEM) ------------------------------------------------------------------------------------------------------------------------------------------------------
Gender bias analysis detected in the text:
This segment of the text 'los alumnos' triggers a EXCLUSIONARY_TERMS bias detection with a score of 0.9



(MessageRole.USER) ------------------------------------------------------------------------------------------------------------------------------------------------------
Proceed to neutralize the original text from the gender biases detected using the debiaser tool.
Keep in mind the 

In [6]:
pd.DataFrame([agent_prediction.model_dump()])

tool_activations  \
0  [{'tool_name': 'gender_bias_classifier', 'tool...   

                                            messages  \
0  [{'role': MessageRole.USER, 'content': 'Mary m...   

                                       llm_responses  \
0  [{'id': 'msg_01TPw5o2gKmHHnMwmvcgetFB', 'type'...   

                                            response  
0  We shouldn't assume Mary likes dolls based on ...

In [7]:
agent_prediction

AgentResponse(tool_activations=[ToolActivation(tool_name='gender_bias_classifier', tool_results={'bias_labels': ['STEREOTYPING_BIAS'], 'bias_texts': ['all girls like playing with dolls'], 'scores': [0.95]}, step_id=1), ToolActivation(tool_name='debiaser', tool_results={'debiasing_text': 'Children have different toy preferences regardless of their gender.', 'reasoning': ["The original text 'Mary must love dolls because all girls like playing with them' contains a strong gender stereotyping bias by assuming that all girls inherently like dolls. This perpetuates harmful gender stereotypes about toy preferences. The text was modified to acknowledge that toy preferences are individual choices not determined by gender, while maintaining a simple and direct structure. The new version removes the assumption about gender-based preferences while keeping the topic of toys and play."]}, step_id=2), ToolActivation(tool_name='debiaser', tool_results={'debiasing_text': "We shouldn't assume Mary likes

In [3]:
train_df = pd.read_excel('../../data/train_val_splits/train_data.xlsx')

train_df["sesgo_pronombre"] = train_df["sesgo_pronombre"]\
    .replace({"Si": "SI", "No": "NO"})

train_df["sesgo_otro"] = train_df["sesgo_otro"].replace({
    "Si": "SI", "si":"SI", "s":"SI",
    "No": "NO", "nO":"NO"
    })
train_df['sesgo_otro'].value_counts()

sesgo_otro
NO     2522
SI     1689
NO        4
N         3
a         2
S         1
Name: count, dtype: int64

In [14]:
def pretty_prompt(biased_samples, unbiased_samples, changes):
    examples = "\n".join(
        [
            f"Example {i+1}:\n"
            f"Biased: {biased}\n"
            f"Unbiased: {unbiased}\n"
            f"Changes: {change}\n"
            for i, (biased, unbiased, change) in enumerate(zip(biased_samples, unbiased_samples, changes))
        ]
    )
    
    prompt = f"""
Below are examples of gender-biased and unbiased phrases used in university communications, as well as description of the changes made:

{examples}
"""
    
    return prompt




def pretty_prompt_2(biased_samples, example_unbiased_samples):
    examples = "\n".join(
        [
            f"Example {i+1}:\n"
            f"Biased: {biased}\n"
            f"Debiased Version: {unbiased_example}\n"
            for i, (biased, unbiased_example) in enumerate(zip(biased_samples, example_unbiased_samples))
        ]
    )
    
    prompt = f"""
Below are examples of gender-biased phrases used in university communications along with suggested unbiased versions:

{examples}

Use these examples as a guide on how biased phrases are identified and what the unbiased versions should look like.
"""
    
    return prompt

In [15]:
# Sample the DataFrame once and use the resulting indices to select the corresponding columns
bias_mask = ~train_df.version_con_sesgo.isna()
num_samples = 5
rnd_state = 666

sampled_df = train_df[bias_mask].sample(num_samples, random_state=rnd_state)
x_train_bias = sampled_df['frases'].tolist()
y_train_bias = sampled_df['version_sin_sesgo'].tolist()
changes_train_bias = sampled_df['description_bias_removal'].tolist()

# sampled_df = [~bias_mask].sample(num_samples, random_state=rnd_state)
# x_train_bias = sampled_df['frases']

# Write the output to a .txt file
file_path = '../../debiasing/llm/biases_example.txt'
file_path2 = '../../debiasing/llm/debiasing_example.txt'

with open(file_path, "w") as file:
    file.write(
        pretty_prompt(x_train_bias, 
                      y_train_bias, 
                      changes_train_bias)
    )
    print(f"Output written to {file_path}")

with open(file_path2, "w") as file:
    file.write(
        pretty_prompt_2(x_train_bias, 
                      y_train_bias,)
    )
    print(f"Output written to {file_path2}")


Output written to ../../debiasing/llm/biases_example.txt
Output written to ../../debiasing/llm/debiasing_example.txt


## Improve agent using validation test

In [8]:
val_df = pd.read_excel('../../data/train_val_splits/val_data.xlsx')
val_df.head(n=3)

index                                             titulo               url  \
0  14186  Atención Secretaría de Estudios jueves 4 de oc...  detalle?id=22733   
1   2906  Comunicado FCFM: Extensión vacaciones invierno...  detalle?id=55461   
2  13936           Mañana en la FCFM - lunes 5 de noviembre  detalle?id=23285   

                                             mensaje               fecha  \
0  Se informa a la comunidad estudiantil que el d... 2018-10-03 10:09:03   
1  Viernes 17 de junio de 2022 \nEstimada comunid... 2022-06-17 11:22:17   
2  WORKSHOP: \n\n"Workshop en Macroeconomía". \n\... 2018-10-31 17:07:31   

                                              frases sesgo_pronombre  \
0  Se informa a la comunidad estudiantil que el d...              NO   
1  Ésta permite el teletrabajo para funcionarias/...              NO   
2              Hora: 16:30 hrs Lugar: Auditorio DIE.             NaN   

  sesgo_otro                                  version_con_sesgo  \
0         SI  Se informa a todos los estudiantes  que el día...   
1         NO  Ésta permite el teletrabajo para funcionarios ...   
2        NaN                                                NaN   

                                   version_sin_sesgo  \
0  Se informa a la comunidad estudiantil que el d...   
1  Ésta permite el teletrabajo para funcionarias/...   
2                                                NaN   

  potencialmente_sesgable_otro_sesgo revisado  \
0                                 SI       SI   
1                                 SI       SI   
2                                NaN       SI   

                            description_bias_removal         biased_words  \
0  Se reemplazó "estudiantes" por "comunidad estu...          estudiantes   
1  Se incluyó la perspectiva femenina en "funcion...  funcionarios, hijos   
2                                                NaN                  NaN   

                   unbiased_words  
0  comunidad estudiantil, Alumn@s  
1       funcionarias/os, hijas/os  
2                             NaN

In [7]:
# Obtener observaciones que presentan sesgo de pronombre y a su vez tienen otro sesgo adicional
try_this = val_df[(val_df['sesgo_otro'] == 'SI') & (val_df['sesgo_pronombre'] == 'SI')]
try_this.shape

(49, 15)

In [8]:
print(try_this.iloc[2]['frases'])

D.- Se recuerda a los alumnos que los cheques deben ser cobrados antes de 60 días contados, desde su fecha de emisión, ya que en caso contrario al caducar el documento este NO será revalidado por los Servicios Centrales.


In [37]:
try_this[:4]

index                                             titulo  \
12  20964  Legalización de Pagaré  Fondo Solidario de Cré...   
56  21176  Postulación a Becas y Créditos Curso Superior ...   
74  21341                  Entrega cheque PAE séptima cuota.   
92   9188                      Beauchef al día - 19 de junio   

                 url                                            mensaje  \
12   detalle?id=8457  Se informa a los estudiantes año de ingreso 20...   
56   detalle?id=8122  Se informa a los estudiantes que hasta el día ...   
74   detalle?id=7942  Se informa a los estudiantes que la entrega de...   
92  detalle?id=32790  Estimada comunidad FCFM: \n_x000D_\nJunto con ...   

                 fecha                                             frases  \
12 2015-03-17 12:35:17  Se informa a los estudiantes año de ingreso 20...   
56 2014-11-25 14:54:25  Se informa a los estudiantes que hasta el día ...   
74 2014-10-15 17:11:15  D.- Se recuerda a los alumnos que los cheques ...   
92 2020-06-19 11:40:19  Astrónomos chilenos crean una aplicación para ...   

   sesgo_pronombre sesgo_otro  \
12              SI         SI   
56              SI         SI   
74              SI         SI   
92              SI         SI   

                                    version_con_sesgo  \
12  Se informa a los estudiantes año de ingreso 20...   
56  Se informa a los slumnos que hasta el día 26 d...   
74  D.- Se recuerda a los alumnos que los cheques ...   
92  Astrónomos chilenos crean una aplicación para ...   

                                    version_sin_sesgo  \
12  Se informa a las/os estudiantes año de ingreso...   
56  Se informa a las/os estudiantes que hasta el d...   
74  D.- Se recuerda a las y los estudiantes  que l...   
92  Astrónomos chilenos crean una aplicación para ...   

   potencialmente_sesgable_otro_sesgo revisado  \
12                                 SI       SI   
56                                 SI       SI   
74                                 SI       SI   
92                                 SI       SI   

                             description_bias_removal  \
12  Se reemplazó el símbolo @ por la forma inclusi...   
56  Se modificó "alumnos" por "las/os estudiantes"...   
74  Se reemplazó "alumnos" por "las y los estudian...   
92  Se incluyó la letra "a" o "os" en los sustanti...   

                                      biased_words  \
12                                l@s, estudiantes   
56                               alumnos, aquellos   
74                                         alumnos   
92  estudiantes, estudiantes secundarios, expertos   

                                       unbiased_words  
12                                    las/os, alumnos  
56        las/os estudiantes, aquellas/os estudiantes  
74                              las y los estudiantes  
92  estudiantes/os, estudiantes secundarias/os, pe...

**TODO:** Pick a good example from the validation set for the diagram...

## Collect predictions from the dataset

In [3]:
test_data_path = '../../data//processed/20231210_test_data_labeled.csv'

test_df = pd.read_csv(test_data_path)
test_df.shape

(853, 6)

In [4]:
test_df.head(n=2)

input  \
0  Estimada comunidad beauchefiana: ¿Tienes papel...   
1  Desde hoy y hasta el 19 de diciembre puedes de...   

                                              target sesgo_pronombre  \
0  ['Estimada comunidad beauchefiana: ¿Tienes pap...              NO   
1  ['Desde hoy y hasta el 19 de diciembre puedes ...             NaN   

  sesgo_otro                                   seq2seq_document  \
0         NO  Eliminar sesgo de género del siguiente texto:\...   
1        NaN  Eliminar sesgo de género del siguiente texto:\...   

                                     causal_document  
0  <human>: ¿Puedes reescribir el siguiente texto...  
1  <human>: ¿Puedes reescribir el siguiente texto...

In [5]:
preds = []
idx_problems = []
problems = []

save_interval = 50

# Initialize agent
debiaser = Debiaser(provider="anthropic")

# Iterate over the dataframe and get the predictions
for idx in range(test_df.shape[0]):
    start = time.time()
    try:
        debiaser_pred = debiaser.predict(
            test_df.loc[idx, 'input']
        ).model_dump()

        debiaser_pred['index'] = idx 

        preds.append(debiaser_pred)
    except Exception as e:
        print(f'Error at index {idx}: {e}')
        idx_problems.append(idx)
        problems.append(e)
    elapsed_time = time.time() - start
    print(f'Elapsed time for processing obs #{idx}: {elapsed_time:.2f} seconds\n-----')

    # Save the dataframe every save_interval obs
    if (idx + 1) % save_interval == 0:
        preds_df = pd.DataFrame(preds)
        preds_df.to_csv('predictions.csv', index=False)
        print(f'Saved predictions up to index {idx}')

        # Save the problems, if any
        if len(idx_problems) > 0:
            pd.DataFrame({
                'index': idx,
                'problem': problems
            }).to_csv('problems.csv', index=False)


# Save the final predictions
print("Saving final predictions")
preds_df = pd.DataFrame(preds)
preds_df.to_csv('predictions.csv', index=False)

# Save the problems, if any
if len(idx_problems) > 0:
    print("Saving idx from observations with problems")
    pd.DataFrame({
        'index': idx_problems,
        'problem': problems
    }).to_csv('problems.csv', index=False)

2025-01-24 17:27:32 - debiasing.configs - INFO - LLM Anthropic response: {"id":"msg_01U1EwuVKTTaQf93KcZJsqSr","type":"message","role":"assistant","model":"claude-3-5-sonnet-20241022","content":[{"type":"text","text":"Let me analyze this Spanish text for potential gender biases using the gender bias classifier tool."},{"type":"tool_use","id":"toolu_01RCP6BQZfNW7XjPnPUp51Mc","name":"gender_bias_classifier","input":{"bias_label":["UNBIASED"],"bias_text":["Estimada comunidad beauchefiana: ¿Tienes papeles acumulados en tu casa?"],"score_label":[1.0]}}],"stop_reason":"tool_use","stop_sequence":null,"usage":{"input_tokens":1668,"cache_creation_input_tokens":0,"cache_read_input_tokens":0,"output_tokens":149}}
2025-01-24 17:27:32 - debiasing.configs - INFO - LLM text: type='text' text='Let me analyze this Spanish text for potential gender biases using the gender bias classifier tool.'
2025-01-24 17:27:32 - debiasing.configs - INFO - LLM tool: type='tool' name='gender_bias_classifier' arguments=

🍩 https://wandb.ai/alcazar90/debiasing-gender-biases/r/call/019499ff-8a17-7dd2-b435-1422c2f7cc41
Elapsed time for processing obs #0: 3.47 seconds
-----


2025-01-24 17:27:34 - debiasing.configs - INFO - LLM Anthropic response: {"id":"msg_0162pYKaevk4bdR3xyZiciHT","type":"message","role":"assistant","model":"claude-3-5-sonnet-20241022","content":[{"type":"text","text":"Let me analyze this Spanish text for potential gender biases using the gender bias classifier tool first."},{"type":"tool_use","id":"toolu_01YGLfN9spNv54DkfDyXczNZ","name":"gender_bias_classifier","input":{"bias_label":["GENERIC_PRONOUNS"],"bias_text":["ellos"],"score_label":[0.8]}}],"stop_reason":"tool_use","stop_sequence":null,"usage":{"input_tokens":1677,"cache_creation_input_tokens":0,"cache_read_input_tokens":0,"output_tokens":129}}
2025-01-24 17:27:34 - debiasing.configs - INFO - LLM text: type='text' text='Let me analyze this Spanish text for potential gender biases using the gender bias classifier tool first.'
2025-01-24 17:27:34 - debiasing.configs - INFO - LLM tool: type='tool' name='gender_bias_classifier' arguments={'bias_label': ['GENERIC_PRONOUNS'], 'bias_tex

🍩 https://wandb.ai/alcazar90/debiasing-gender-biases/r/call/019499ff-97a7-7050-b3a6-f858321f4993
Elapsed time for processing obs #1: 6.22 seconds
-----


2025-01-24 17:27:42 - debiasing.configs - INFO - LLM Anthropic response: {"id":"msg_01JvXs8CLLqE5NeKRKMrSVPd","type":"message","role":"assistant","model":"claude-3-5-sonnet-20241022","content":[{"type":"text","text":"Let me analyze this text for potential gender biases using the gender bias classifier first."},{"type":"tool_use","id":"toolu_01Mbj5ALiMBHZLKV54168a6P","name":"gender_bias_classifier","input":{"bias_label":["UNBIASED"],"bias_text":["Revisa en el afiche qué tipo de papeles puedes traer, los estarán recibiendo en el edificio Escuela, bajo la escalera principal."],"score_label":[1.0]}}],"stop_reason":"tool_use","stop_sequence":null,"usage":{"input_tokens":1682,"cache_creation_input_tokens":0,"cache_read_input_tokens":0,"output_tokens":162}}
2025-01-24 17:27:42 - debiasing.configs - INFO - LLM text: type='text' text='Let me analyze this text for potential gender biases using the gender bias classifier first.'
2025-01-24 17:27:42 - debiasing.configs - INFO - LLM tool: type='too

...

Request failed: HTTPSConnectionPool(host='api.anthropic.com', port=443): Max retries exceeded with url: /v1/messages (Caused by ConnectTimeoutError(<urllib3.connection.HTTPSConnection object at 0x12be72850>, 'Connection to api.anthropic.com timed out. (connect timeout=15)'))
🍩 https://wandb.ai/alcazar90/debiasing-gender-biases/r/call/01949a5d-c49a-7512-81eb-7f22ded1748d
Elapsed time for processing obs #850: 15.02 seconds
-----


2025-01-24 19:10:54 - debiasing.configs - INFO - LLM text: HTTPSConnectionPool(host='api.anthropic.com', port=443): Max retries exceeded with url: /v1/messages (Caused by ConnectTimeoutError(<urllib3.connection.HTTPSConnection object at 0x12bef07d0>, 'Connection to api.anthropic.com timed out. (connect timeout=15)'))
2025-01-24 19:10:54 - debiasing.configs - INFO - LLM tool: None


Request failed: HTTPSConnectionPool(host='api.anthropic.com', port=443): Max retries exceeded with url: /v1/messages (Caused by ConnectTimeoutError(<urllib3.connection.HTTPSConnection object at 0x12bef07d0>, 'Connection to api.anthropic.com timed out. (connect timeout=15)'))
🍩 https://wandb.ai/alcazar90/debiasing-gender-biases/r/call/01949a5d-ff49-7c53-af95-1cc8e9aa15dc
Elapsed time for processing obs #851: 15.03 seconds
-----


2025-01-24 19:11:09 - debiasing.configs - INFO - LLM text: HTTPSConnectionPool(host='api.anthropic.com', port=443): Max retries exceeded with url: /v1/messages (Caused by ConnectTimeoutError(<urllib3.connection.HTTPSConnection object at 0x12beac7d0>, 'Connection to api.anthropic.com timed out. (connect timeout=15)'))
2025-01-24 19:11:09 - debiasing.configs - INFO - LLM tool: None


Request failed: HTTPSConnectionPool(host='api.anthropic.com', port=443): Max retries exceeded with url: /v1/messages (Caused by ConnectTimeoutError(<urllib3.connection.HTTPSConnection object at 0x12beac7d0>, 'Connection to api.anthropic.com timed out. (connect timeout=15)'))
🍩 https://wandb.ai/alcazar90/debiasing-gender-biases/r/call/01949a5e-39fd-7840-805a-db66eab7168b
Elapsed time for processing obs #852: 15.03 seconds
-----
Saving final predictions
Saving idx from observations with problems


In [6]:
debiaser_results = pd.read_csv('predictions.csv')
debiaser_results.head(n=4)

input            biases scores  \
0  Estimada comunidad beauchefiana: ¿Tienes papel...          UNBIASED    1.0   
1  Desde hoy y hasta el 19 de diciembre puedes de...  GENERIC_PRONOUNS    0.8   
2  Revisa en el afiche qué tipo de papeles puedes...          UNBIASED    1.0   
3                                    ¡Les esperamos!          UNBIASED    1.0   

                                    debias_reasoning  \
0                                                NaN   
1  Se detectó un sesgo de GENERIC_PRONOUNS en el ...   
2                                                NaN   
3                                                NaN   

                                              output  index  
0                                           UNBIASED      0  
1  Desde hoy y hasta el 19 de diciembre puedes de...      1  
2                                           UNBIASED      2  
3                                           UNBIASED      3

In [8]:
debiaser_results

input              biases  \
0    Estimada comunidad beauchefiana: ¿Tienes papel...            UNBIASED   
1    Desde hoy y hasta el 19 de diciembre puedes de...    GENERIC_PRONOUNS   
2    Revisa en el afiche qué tipo de papeles puedes...            UNBIASED   
3                                      ¡Les esperamos!            UNBIASED   
4    Estimada Comunidad:   La Subdirección de Puebl...  EXCLUSIONARY_TERMS   
..                                                 ...                 ...   
814  Desde la Unidad de Bienestar Estudiantil se es...                 NaN   
815  Quienes se encuentran en estado de afectación ...                 NaN   
816  Agradecemos la flexibilidad de todas y todos p...                 NaN   
817  La Escuela de Ingeniería y Ciencias está monit...                 NaN   
818  Atentamente,  Ricardo Herrera Mardones Directo...                 NaN   

    scores                                   debias_reasoning  \
0      1.0                                                NaN   
1      0.8  Se detectó un sesgo de GENERIC_PRONOUNS en el ...   
2      1.0                                                NaN   
3      1.0                                                NaN   
4      0.8  El término 'ayudante' aunque gramaticalmente e...   
..     ...                                                ...   
814    NaN                                                NaN   
815    NaN                                                NaN   
816    NaN                                                NaN   
817    NaN                                                NaN   
818    NaN                                                NaN   

                                                output  index  
0                                             UNBIASED      0  
1    Desde hoy y hasta el 19 de diciembre puedes de...      1  
2                                             UNBIASED      2  
3                                             UNBIASED      3  
4    Estimada Comunidad:   La Subdirección de Puebl...      4  
..                                                 ...    ...  
814                                           UNBIASED    848  
815                                           UNBIASED    849  
816                                           UNBIASED    850  
817                                           UNBIASED    851  
818                                           UNBIASED    852  

[819 rows x 6 columns]

In [10]:
debiaser_results.output.value_counts()

output
UNBIASED                                                                                                                                                                                                                                                                                                                                                 635
El estudiantado debe LEER LAS BASES Y REALIZAR su postulación a través del FORMULARIO                                                                                                                                                                                                                                                                      2
Completa el formulario y adjunta la documentación de respaldo en el siguiente LINK Plazos:   - General: hasta el 10 de diciembre - Programa de Residencia Universitaria: hasta el 24 de noviembre    Si ingresaste vía SIPEE , PACE o renuevas el Programa de Residencia, recibirás un correo para agen